<a href="https://colab.research.google.com/github/25stu0709-jpg/yolov8_yolov11_guide/blob/main/yolov11_video.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [12]:
# ============================================
# YOLOv11 × YouTube Shorts × CSV 저장 (축소 + 안전 통합)
# ============================================

# 1️⃣ 라이브러리 설치
!pip install ultralytics yt_dlp opencv-python-headless ffmpeg-python pandas -q

import yt_dlp, ffmpeg, os, pandas as pd
from ultralytics import YOLO
from IPython.display import Video, display
from glob import glob

# ============================================
# 2️⃣ 유튜브 영상 다운로드
# ============================================
youtube_url = "https://youtube.com/shorts/IAeOLqOxKz8?si=hvX5vBt5-vkGpcMN"
full_video = "full_video.mp4"
clip_video = "clip_30s_halfsize.mp4"

print("🎥 영상 다운로드 중...")
ydl_opts = {"format": "mp4", "outtmpl": full_video, "quiet": True}

try:
    with yt_dlp.YoutubeDL(ydl_opts) as ydl:
        ydl.download([youtube_url])
    print("✅ 다운로드 완료!")
except Exception as e:
    print("❌ 영상 다운로드 오류:", e)

# ============================================
# 3️⃣ 영상 처음 30초 + 원본 1/2 크기
# ============================================
print("✂️ 영상 처음 30초 추출 + 크기 1/2 축소 중...")
try:
    probe = ffmpeg.probe(full_video)
    video_streams = [s for s in probe['streams'] if s['codec_type'] == 'video']
    if len(video_streams) == 0:
        raise ValueError("⚠️ 비디오 스트림을 찾을 수 없습니다.")

    width = int(video_streams[0]['width'])
    height = int(video_streams[0]['height'])
    half_width = width // 2
    half_height = height // 2

    ffmpeg.input(full_video, t=30).filter('scale', half_width, half_height)\
        .output(clip_video, vcodec='libx264', acodec='aac', strict='experimental')\
        .overwrite_output().run(quiet=True)

    print(f"✅ 30초 클립 저장 완료 (1/2 크기): {clip_video}")
except Exception as e:
    print("❌ 영상 처리 오류:", e)

# ============================================
# 4️⃣ YOLOv11 모델 로드
# ============================================
print("🔍 YOLOv11 모델 로드 중...")
try:
    model = YOLO("yolov11n.pt")  # 가벼운 모델
    print("✅ YOLOv11n 모델 로드 완료")
except Exception as e:
    print("❌ 모델 로드 오류:", e)

# ============================================
# 5️⃣ 객체 탐지 실행
# ============================================
print("🔎 객체 인식 중...")
results = None
try:
    results = model.predict(
        source=clip_video,
        conf=0.5,
        save=True,
        save_video=True,  # 🎯 결과 영상 저장
        show=False
    )
    print("✅ 객체 인식 완료!")
except Exception as e:
    print("❌ 탐지 오류:", e)

# ============================================
# 6️⃣ 탐지 결과 CSV 저장
# ============================================
if results is not None:
    print("📊 탐지 결과 CSV 저장 중...")
    csv_data = []
    for r in results:
        boxes = r.boxes
        for box in boxes:
            x1, y1, x2, y2 = box.xyxy[0].tolist()
            conf = float(box.conf[0])
            cls_id = int(box.cls[0])
            cls_name = model.names[cls_id]
            csv_data.append([cls_name, conf, x1, y1, x2, y2])

    csv_file = "yolo_detections.csv"
    df = pd.DataFrame(csv_data, columns=["class", "confidence", "x1", "y1", "x2", "y2"])
    df.to_csv(csv_file, index=False)
    print(f"✅ CSV 저장 완료: {csv_file}")
else:
    print("⚠️ 객체 인식 결과가 없어 CSV를 저장하지 않습니다.")

# ============================================
# 7️⃣ 결과 영상 Colab에서 재생
# ============================================
result_path = None
output_dir = "runs/detect"
detect_folders = sorted(glob(os.path.join(output_dir, "*")))
if detect_folders:
    latest_run = detect_folders[-1]
    # YOLOv11 저장 영상 경로
    candidate_video = os.path.join(latest_run, os.path.basename(clip_video))
    if os.path.exists(candidate_video):
        result_path = candidate_video

if result_path and os.path.exists(result_path):
    display(Video(result_path, embed=True))
else:
    if os.path.exists(clip_video):
        display(Video(clip_video, embed=True))
    else:
        print("⚠️ 영상 파일을 찾을 수 없습니다.")


🎥 영상 다운로드 중...


         player = https://www.youtube.com/s/player/7b9b4e02/player_ias.vflset/en_US/base.js
         n = VXfuBY2aLcpmynD5twu ; player = https://www.youtube.com/s/player/7b9b4e02/player_ias.vflset/en_US/base.js
         Please report this issue on  https://github.com/yt-dlp/yt-dlp/issues?q= , filling out the appropriate issue template. Confirm you are on the latest version using  yt-dlp -U


✅ 다운로드 완료!
✂️ 영상 처음 30초 추출 + 크기 1/2 축소 중...
✅ 30초 클립 저장 완료 (1/2 크기): clip_30s_halfsize.mp4
🔍 YOLOv11 모델 로드 중...
❌ 모델 로드 오류: [Errno 2] No such file or directory: 'yolov11n.pt'
🔎 객체 인식 중...
❌ 탐지 오류: name 'model' is not defined
⚠️ 객체 인식 결과가 없어 CSV를 저장하지 않습니다.
